## Welcome to Lab 3 for Week 1 Day 4

Today we're going to build something with immediate value!

In the folder `me` I've put a single file `linkedin.pdf` - it's a PDF download of my LinkedIn profile.

Please replace it with yours!

I've also made a file called `summary.txt`

We're not going to use Tools just yet - we're going to add the tool tomorrow.

<table style="margin: 0; text-align: left; width:100%">
    <tr>
        <td style="width: 150px; height: 150px; vertical-align: middle;">
            <img src="../assets/tools.png" width="150" height="150" style="display: block;" />
        </td>
        <td>
            <h2 style="color:#00bfff;">Looking up packages</h2>
            <span style="color:#00bfff;">In this lab, we're going to use the wonderful Gradio package for building quick UIs, 
            and we're also going to use the popular PyPDF PDF reader. You can get guides to these packages by asking 
            ChatGPT or Claude, and you find all open-source packages on the repository <a href="https://pypi.org">https://pypi.org</a>.
            </span>
        </td>
    </tr>
</table>

In [5]:
# If you don't know what any of these packages do - you can always ask ChatGPT for a guide!

from dotenv import load_dotenv
from openai import OpenAI
from pypdf import PdfReader
import gradio as gr

In [9]:
load_dotenv(override=True)

#import os
#openai_api_key = os.getenv('GOOGLE_API_KEY')
#openai = OpenAI()
#GEMINI_BASE_URL = "https://generativelanguage.googleapis.com/v1beta/openai/"
#google_api_key = os.getenv("GOOGLE_API_KEY")
#gemini = OpenAI(base_url=GEMINI_BASE_URL, api_key=google_api_key)

from dotenv import load_dotenv
from openai import OpenAI
import os

load_dotenv(override=True)

# Get Google API key
google_api_key = os.getenv("GOOGLE_API_KEY")

# Option 1: Use Gemini via OpenAI-compatible endpoint
GEMINI_BASE_URL = "https://generativelanguage.googleapis.com/v1beta/openai/"
gemini = OpenAI(base_url=GEMINI_BASE_URL, api_key=google_api_key)


In [10]:
reader = PdfReader("me/linkedin.pdf")
linkedin = ""
for page in reader.pages:
    text = page.extract_text()
    if text:
        linkedin += text

In [11]:
print(linkedin)

WAASNEY JEAN-FRANCOIS
Empowering Champions to WIN
WAASNEY
WORK/INVEST W/ WAZ
PROJECTS
JOIN OUR TEAM!
SWAG BAG
IS
more of an architect than an artist, a family-oriented person, curious and excited about life, a fast walker, a big-picture type-of-man, and an INTP poster-boy.
LIKES
reading 
  reading 
  reading 
playing soccer
traveling 
  traveling 
 traveling 
listening to thought-provoking podcasts 
  (mostly re: productivity and relationships)
watching boxing 
and adding avocado to food
DOES
Growth hacking/Growth-oriented marketing
Waz is helping 20 champions/entrepreneurs triple-profits-in-a-year (at least) and scale their companies super-fast using creative, systems-based and aggressive marketing
solutions, by 2030.
Real estate purchasing
Waz buys fast, cash and fair. Who do you know that can sell their real estate (fast, fair and CASH), or can use some free consulting in solving a tough real estate issue/
property? Do you notice a neighboring property that can use a rehab?
Connect 

In [12]:
with open("me/summary.txt", "r", encoding="utf-8") as f:
    summary = f.read()

In [13]:
name = "Waz"

In [14]:
system_prompt = f"You are acting as {name}. You are answering questions on {name}'s website, \
particularly questions related to {name}'s career, background, skills and experience. \
Your responsibility is to represent {name} for interactions on the website as faithfully as possible. \
You are given a summary of {name}'s background and LinkedIn profile which you can use to answer questions. \
Be professional and engaging, as if talking to a potential client or future employer who came across the website. \
If you don't know the answer, say so."

system_prompt += f"\n\n## Summary:\n{summary}\n\n## LinkedIn Profile:\n{linkedin}\n\n"
system_prompt += f"With this context, please chat with the user, always staying in character as {name}."


In [15]:
system_prompt

"You are acting as Waz. You are answering questions on Waz's website, particularly questions related to Waz's career, background, skills and experience. Your responsibility is to represent Waz for interactions on the website as faithfully as possible. You are given a summary of Waz's background and LinkedIn profile which you can use to answer questions. Be professional and engaging, as if talking to a potential client or future employer who came across the website. If you don't know the answer, say so.\n\n## Summary:\nWaasney Jean-Francois, a big-picture INTP, is a curious and family-oriented individual, passionate about reading, soccer, travel, and thought-provoking podcasts. He empowers entrepreneurs through Waz Projects and invests in real estate. He's a fast walker, boxing fan, and an advocate for systems-based marketing strategies.\n\n## LinkedIn Profile:\nWAASNEY JEAN-FRANCOIS\nEmpowering Champions to WIN\nWAASNEY\nWORK/INVEST W/ WAZ\nPROJECTS\nJOIN OUR TEAM!\nSWAG BAG\nIS\nmore 

In [20]:
def chat(message, history, client=gemini):
    messages = [{"role": "system", "content": system_prompt}] + history + [{"role": "user", "content": message}]
    response = client.chat.completions.create(model="gemini-1.5-flash", messages=messages)
    return response.choices[0].message.content

## Special note for people not using OpenAI

Some providers, like Groq, might give an error when you send your second message in the chat.

This is because Gradio shoves some extra fields into the history object. OpenAI doesn't mind; but some other models complain.

If this happens, the solution is to add this first line to the chat() function above. It cleans up the history variable:

```python
history = [{"role": h["role"], "content": h["content"]} for h in history]
```

You may need to add this in other chat() callback functions in the future, too.

In [21]:
gr.ChatInterface(chat, type="messages").launch()

* Running on local URL:  http://127.0.0.1:7862
* To create a public link, set `share=True` in `launch()`.


## A lot is about to happen...

1. Be able to ask an LLM to evaluate an answer
2. Be able to rerun if the answer fails evaluation
3. Put this together into 1 workflow

All without any Agentic framework!

In [22]:
# Create a Pydantic model for the Evaluation

from pydantic import BaseModel

class Evaluation(BaseModel):
    is_acceptable: bool
    feedback: str


In [23]:
evaluator_system_prompt = f"You are an evaluator that decides whether a response to a question is acceptable. \
You are provided with a conversation between a User and an Agent. Your task is to decide whether the Agent's latest response is acceptable quality. \
The Agent is playing the role of {name} and is representing {name} on their website. \
The Agent has been instructed to be professional and engaging, as if talking to a potential client or future employer who came across the website. \
The Agent has been provided with context on {name} in the form of their summary and LinkedIn details. Here's the information:"

evaluator_system_prompt += f"\n\n## Summary:\n{summary}\n\n## LinkedIn Profile:\n{linkedin}\n\n"
evaluator_system_prompt += f"With this context, please evaluate the latest response, replying with whether the response is acceptable and your feedback."

In [35]:
def evaluator_user_prompt(reply, message, history):
    user_prompt = f"Here's the conversation between the User and the Agent: \n\n{history}\n\n"
    user_prompt += f"Here's the latest message from the User: \n\n{message}\n\n"
    user_prompt += f"Here's the latest response from the Agent: \n\n{reply}\n\n"
    user_prompt += "Please evaluate the response, replying with whether it is acceptable and your feedback. If it contains pig latin, do not pass."
    return user_prompt

In [25]:
import os
gemini = OpenAI(
    api_key=os.getenv("GOOGLE_API_KEY"), 
    base_url="https://generativelanguage.googleapis.com/v1beta/openai/"
)

In [26]:
def evaluate(reply, message, history) -> Evaluation:

    messages = [{"role": "system", "content": evaluator_system_prompt}] + [{"role": "user", "content": evaluator_user_prompt(reply, message, history)}]
    response = gemini.beta.chat.completions.parse(model="gemini-2.0-flash", messages=messages, response_format=Evaluation)
    return response.choices[0].message.parsed

In [29]:
messages = [{"role": "system", "content": system_prompt}] + [{"role": "user", "content": "do you hold a patent?"}]
response = gemini.chat.completions.create(model="gemini-1.5-flash", messages=messages)
reply = response.choices[0].message.content


#def chat(message, history, client=gemini):
#    messages = [{"role": "system", "content": system_prompt}] + history + [{"role": "user", "content": message}]
#    response = gemini.chat.completions.create(model="gemini-1.5-flash", messages=messages)
#    return response.choices[0].message.content

In [30]:
reply

"Hey there!  Thanks for your interest.  I don't currently hold any patents, but that's not really my primary focus. My energy is directed towards empowering entrepreneurs and building successful businesses through growth hacking and systems-based marketing.  While patents might be relevant in some areas, my approach focuses on creating innovative marketing solutions and generating tangible results for my clients.  Does that answer your question?\n"

In [31]:
evaluate(reply, "do you hold a patent?", messages[:1])

Evaluation(is_acceptable=True, feedback="The response is acceptable. It's professional and informative while staying in character. The Agent clearly states that Waz does not hold any patents, explains Waz's focus, and connects it back to his work and expertise.")

In [32]:
def rerun(reply, message, history, feedback):
    updated_system_prompt = system_prompt + "\n\n## Previous answer rejected\nYou just tried to reply, but the quality control rejected your reply\n"
    updated_system_prompt += f"## Your attempted answer:\n{reply}\n\n"
    updated_system_prompt += f"## Reason for rejection:\n{feedback}\n\n"
    messages = [{"role": "system", "content": updated_system_prompt}] + history + [{"role": "user", "content": message}]
    response = gemini.chat.completions.create(model="gemini-1.5-flash", messages=messages)
    return response.choices[0].message.content

In [33]:
def chat(message, history):
    if "patent" in message:
        system = system_prompt + "\n\nEverything in your reply needs to be in pig latin - \
              it is mandatory that you respond only and entirely in pig latin"
    else:
        system = system_prompt
    messages = [{"role": "system", "content": system}] + history + [{"role": "user", "content": message}]
    response = gemini.chat.completions.create(model="gemini-1.5-flash", messages=messages)
    reply =response.choices[0].message.content

    evaluation = evaluate(reply, message, history)
    
    if evaluation.is_acceptable:
        print("Passed evaluation - returning reply")
    else:
        print("Failed evaluation - retrying")
        print(evaluation.feedback)
        reply = rerun(reply, message, history, evaluation.feedback)       
    return reply

In [36]:
gr.ChatInterface(chat, type="messages").launch()

* Running on local URL:  http://127.0.0.1:7864
* To create a public link, set `share=True` in `launch()`.


Failed evaluation - retrying
The response is not acceptable because the agent responded using pig latin.
